In [5]:
import json
import numpy
import csv
import openai
import time
import os
from dotenv import load_dotenv
import codecs
import multiprocessing
load_dotenv('.env')
from prompts import create_llm_classification_prompt, MISC_DICTS
from utils import *
from tqdm import tqdm

In [6]:
create_llm_classification_prompt(MISC_DICTS)

1. Behavior: Advise with Permission (ADP) 
	Definition: The counselor gives advice, makes a suggestion, or offers a solution or possible action with prior permission from the client. Permission can be directly asked, requested by the client, or given indirectly by allowing the client to disregard the advice. Differentiation: Advise should not be confused with Direct or Question. For example, 'Don't let your friends drink at your house.' is Direct due to the imperative 'Don't'. 'Could you ask your friends not to drink at your house?' is a Closed Question. 'What could you ask your friends to do to help you?' is an Open Question.
	Examples: ['Would it be all right if I suggested something?', 'We could try brainstorming to come up with ideas about quitting if you like.']

2. Behavior: Advise without Permission (ADW) 
	Definition: The counselor gives advice, makes a suggestion, or offers a solution or possible action without seeking prior permission from the client. Differentiation: Advise 

'1. Behavior: Advise with Permission (ADP) \n\tDefinition: The counselor gives advice, makes a suggestion, or offers a solution or possible action with prior permission from the client. Permission can be directly asked, requested by the client, or given indirectly by allowing the client to disregard the advice. Differentiation: Advise should not be confused with Direct or Question. For example, \'Don\'t let your friends drink at your house.\' is Direct due to the imperative \'Don\'t\'. \'Could you ask your friends not to drink at your house?\' is a Closed Question. \'What could you ask your friends to do to help you?\' is an Open Question.\n\tExamples: [\'Would it be all right if I suggested something?\', \'We could try brainstorming to come up with ideas about quitting if you like.\']\n\n2. Behavior: Advise without Permission (ADW) \n\tDefinition: The counselor gives advice, makes a suggestion, or offers a solution or possible action without seeking prior permission from the client. D

In [7]:
csv_path = "AnnoMI-simple.csv"
with open(csv_path, mode='r') as file:
    csv_reader = csv.reader(file)
    transcripts = [row for row in csv_reader]
header = transcripts.pop(0)
dict_list = [dict(zip(header, row)) for row in transcripts]

In [8]:
import csv

csv_path = "AnnoMI-simple.csv"

# Open the CSV file and read the content
with open(csv_path, mode='r') as file:
    csv_reader = csv.reader(file)
    # Extract headers (assume the first row contains headers)
    headers = next(csv_reader)
    # Create a list of dictionaries
    dict_list = [dict(zip(headers, row)) for row in csv_reader]

print(dict_list)


[{'transcript_id': '0', 'mi_quality': 'high', 'video_title': 'NEW VIDEO: Brief intervention: "Barbara"', 'video_url': 'https://www.youtube.com/watch?v=PaSKcfTmFEk', 'topic': 'reducing alcohol consumption', 'utterance_id': '0', 'interlocutor': 'therapist', 'timestamp': '00:00:13', 'utterance_text': 'Thanks for filling it out. We give this form to everyone once a year regardless of why they come in. It helps us provide better care. Is it okay if I take a look at what you put down?', 'main_therapist_behaviour': 'question', 'client_talk_type': 'n/a'}, {'transcript_id': '0', 'mi_quality': 'high', 'video_title': 'NEW VIDEO: Brief intervention: "Barbara"', 'video_url': 'https://www.youtube.com/watch?v=PaSKcfTmFEk', 'topic': 'reducing alcohol consumption', 'utterance_id': '1', 'interlocutor': 'client', 'timestamp': '00:00:24', 'utterance_text': 'Sure.', 'main_therapist_behaviour': 'n/a', 'client_talk_type': 'neutral'}, {'transcript_id': '0', 'mi_quality': 'high', 'video_title': 'NEW VIDEO: Bri

In [9]:
def get_message_single(utterance):
    # therapist_prompt_path = ""
    # client_prompt_path = ""
    utterance_text = utterance["utterance_text"]
    speaker = utterance["interlocutor"]
    if speaker == "therapist":
        prompt_path = "prompts/prompt"
    else:
        raise Exception("dont give me a client")

    with open(prompt_path, 'r') as f:
        prompt = f.read()

    #deal with the prompt, add the utterances and all that
    # message = "where do you think this conversation is taking place? reply only with 'cool' if the room seems chilly or 'uncool' it seems hot\n"
    # message += f"{speaker}: {utterance_text}"
    message = prompt.format(utterance_text=utterance_text)
    formated_message = [{"role": "user", "content": message}]
    return formated_message

In [10]:
def get_message_parallel(jsons):
    # therapist_prompt_path = ""
    # client_prompt_path = ""
    therapist_utterances = []
    for utterance in jsons:
        speaker = utterance["interlocutor"]
        if speaker == "therapist":
            therapist_utterances.append(utterance["utterance_text"])
    
    prompt_path = "prompts/prompt_parallel"
    with open(prompt_path, 'r') as f:
        prompt = f.read()
    # print(therapist_utterances)
    message = prompt.format(therapist_utterances=str(therapist_utterances))
    # print(message)

    formated_message = [{"role": "user", "content": message}]
    return formated_message

In [7]:
def reply_from_utterance(utterance):
    message = get_message_single(utterance)
    return get_completion_from_messages(messages=message)

def reply_from_utterance_parallel(conversation):
    message = get_message_parallel(conversation)
    return get_completion_from_messages(messages=message)

In [8]:
# dir_path = "annotated_data"

# curr_id = dict_list[0]["transcript_id"]
# convo_list = []
# convo = []

# for utterance in dict_list:
#     if utterance['transcript_id'] != curr_id:
#         try:
#             file.close()
#         except:
#             pass
#         curr_id = utterance['transcript_id']
#         convo_list.append(convo)
#     convo.append(utterance)

#     message = get_message(utterance)
#     # reply = get_completion_from_messages(messages=message)
#     reply = file_name
#     utterance["llm_classification"] = reply
#     print(json.dumps(utterance), file=file)
# file.close()

In [9]:
#get all predictions in parallel. conversation is passed as one. Having issues with interpreting this many at once
def classify_conversation(dict_list, dir_path='annotated_data'):

    curr_id = '0'

    utterance = dict_list[0]
    curr_id = utterance['transcript_id']
    quality = utterance['mi_quality']
    file_name = f"{curr_id}_{quality}"
    file_path = os.path.join(dir_path, file_name)
    file = codecs.open(file_path, 'w', 'utf-8')

    conversation = []
    i = 0
    for utterance in tqdm(dict_list):
        i += 1
        if utterance['transcript_id'] != curr_id:
            reply = reply_from_utterance_parallel(conversation)
            reply = reply[1:-1].split(", ")
            reply_id = 0
            for utter in conversation:
                if utter["interlocutor"] == "therapist":   
                    utter["llm_classification"] = reply[reply_id]
                    reply_id += 1
                else:
                    utter["llm_classification"] = "n/a"
                print(json.dumps(utter), file=file)
            if reply_id != len(reply):
                print(f"not all replies assigned to an utterance. check {file_name}. at reply index {reply_id}. reply was {reply}")
            
            conversation = []
            file.close()
            break
            curr_id = utterance['transcript_id']
            quality = utterance['mi_quality']
            file_name = f"{curr_id}_{quality}"
            file_path = os.path.join(dir_path, file_name)
            file = codecs.open(file_path, 'w', 'utf-8')

        # if utterance["interlocutor"] == "therapist":
        conversation.append(utterance)

    file.close()

# classify_conversation(dict_list)

In [10]:
#get all predictions in parallel. n predictions at a time
def classify_n_ata_time(dict_list, dir_path='annotated_data', n=5, skip_convo=[]):
    
    utterance = dict_list[0]
    curr_id = utterance['transcript_id']
    quality = utterance['mi_quality']
    file_name = f"{curr_id}_{quality}"
    file_path = os.path.join(dir_path, file_name)
    file = codecs.open(file_path, 'w', 'utf-8')

    conversation = []
    therapist_utterances = 0
    for utterance in tqdm(dict_list):
        if utterance['transcript_id'] != curr_id or therapist_utterances >= n:
            reply = reply_from_utterance_parallel(conversation)
            # print(reply)
            reply = reply[1:-1].split(", ")
            reply_id = 0
            # print(f"getting replies for conversation of length {len(conversation)}")
            # print(reply)
            # print(conversation)
            for utter in conversation:
                if utter["interlocutor"] == "therapist":   
                    utter["llm_classification"] = reply[reply_id]
                    reply_id += 1
                else:
                    utter["llm_classification"] = "n/a"
                # print(json.dumps(utter), file=file)
        # print(f'got {len(reply)} replies and wrote')

            if reply_id != len(reply):
                print(conversation)
                print(f"not all replies assigned to an utterance. check {file_name}. at reply index {reply_id}. reply was {reply}")
            conversation = []
            therapist_utterances = 0
            if utterance['transcript_id'] != curr_id:
                file.close()
                curr_id = utterance['transcript_id']
                quality = utterance['mi_quality']
                file_name = f"{curr_id}_{quality}"
                file_path = os.path.join(dir_path, file_name)
                file = codecs.open(file_path, 'w', 'utf-8')


        if utterance["interlocutor"] == "therapist":
            therapist_utterances += 1
        conversation.append(utterance)

    file.close()
classify_n_ata_time(dict_list[798:], n=8)

  0%|          | 0/8901 [00:00<?, ?it/s]

["So I get a sense it's a little anxious being here today and, uh, meeting someone like me, and, um, what we're gonna be doing today is-is inducting, but also I wanna talk about, um, yeah, the issues that-that have got you here and we need to do some sorting out around, um, yeah how serious you are to sort of sort those issues. So?", 'Sorry?', 'All right.', 'Yeah.', 'So first, it might be trying to sort out what are the important issues to sort out.', "Yeah, that makes sense? Yeah? So how confident are you that-that, you know, you can sort out the issues related to, um, you know, uh, taking the money from your employer? And another thing, in your precinct's report, there were some issues around gambling, and some issues around alcohol use. So those seem to be important issues that are kind of getting out. So how confident are you that you can get those sorted in the nine months we've got?", 'Yeah.', 'Yeah, yeah.']


  0%|          | 15/8901 [00:09<1:34:01,  1.58it/s]

You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.
error
['rro']
[{'transcript_id': '18', 'mi_quality': 'high', 'video_title': 'Motivational Techniques - Ken interviews Catherine - 1', 'video_url': 'https://www.youtube.com/watch?v=PM1q6uB0ysQ', 'topic': 'reducing gambling', 'utterance_id': '0', 'interlocutor': 'therapist', 'timestamp': '00:01:20', 'utterance_text': "So I get a sense it's a little anxious being here today and, uh, meeting someone like me, and, um, what we're gonna be doing today is-is inducting, but also I wanna talk about, um, yeah, the issues that-that have got you here and we need to do some sorting out around, um, yeah how serious you are to sort of sort those issues. So?", 'main_therapist_behaviour': 'reflection', 'client_talk_type': 'n/a'}, {'transcript_id': '18', 'mi_quality': 'high', 'video_title': 'Motivational Techniques 

IndexError: list index out of range

In [14]:
for i, u in enumerate(dict_list):
    if u["transcript_id"] == "18":
        print(i)
        break

798


In [16]:
def classify_single(dict_list, dir_path = "annotated_data_single"):


    curr_id = "-1"

    utterance = dict_list[0]
    curr_id = utterance['transcript_id']
    quality = utterance['mi_quality']
    file_name = f"{curr_id}_{quality}"
    file_path = os.path.join(dir_path, file_name)
    file = codecs.open(file_path, 'w', 'utf-8')

    for utterance in dict_list:
        if utterance['transcript_id'] != curr_id:
            try:
                file.close()
            except:
                pass
            curr_id = utterance['transcript_id']
            quality = utterance['mi_quality']
            file_name = f"{curr_id}_{quality}"
            file_path = os.path.join(dir_path, file_name)
            file = codecs.open(file_path, 'w', 'utf-8')
            break

        if utterance["interlocutor"] != "therapist":
            utterance["llm_classification"] = "n/a"
            print(json.dumps(utterance), file=file)
            continue
        message = get_message_single(utterance)
        reply = get_completion_from_messages(messages=message)
        # reply = file_name
        utterance["llm_classification"] = reply
        print(json.dumps(utterance), file=file)
    file.close()

In [36]:
def pretty_print(path):
    with open(path, 'r') as f:
        for line in f:
            js = json.loads(line)
            message = js['interlocutor']
            if message == "therapist":
                message += f" ({js['llm_classification']})"
            message += f": {js['utterance_text']}"
            print(message)

pretty_print("annotated_data/0_high")

therapist ("ST"): Thanks for filling it out. We give this form to everyone once a year regardless of why they come in. It helps us provide better care. Is it okay if I take a look at what you put down?
client: Sure.
therapist ("GI"): So, let's see. It looks that you put-- You drink alcohol at least four times a week on average-
client: Mm-hmm.
therapist ("GI"): -and you usually have three to four drinks when you do drink.
client: Usually three drinks and glasses of wine.
therapist ("RES"): Okay. That's at least 12 drinks a week.
client: Something like that.
therapist ("ST"): Okay. Just so you know, my role, um, when we talk about alcohol use, is just to share information about risk and to help patients who want help. This is different than telling them what I think they should do. I don't do that.
client: Okay.
therapist ("QUO"): Uh, what else can you tell me about your drinking.
client: Well, I usually drink when I'm at home trying to unwind and I drink while I'm watching a movie. And

In [11]:
pretty_print("annotated_data/13_high")

therapist (ST): Hi, Mrs. Smith. I wanted to let you know that at this appointment, we're gonna be giving Lilly some vaccines.
client: Oh, I-I don't know if I'm comfortable with that. I've been reading a bunch of stuff lately about them.
therapist (QUO): Hmm. Can you tell me more about your concerns about vaccines?
client: Uh, yeah, well, I was just- I was reading that it's better to let them build up their immunity, like, naturally and stuff in their immune systems.
therapist (REC): Okay, so you were thinking that maybe exposing Lily naturally to these diseases would be a better choice than using vaccines to help her get stronger?
client: Well, yeah. I mean, I had chickenpox as a kid, and now I'm immune. Right? So.
therapist (RCP): That's right. Having chickenpox as a child means that you are less likely to have chickenpox as an adult because you've developed a-a natural immunity. Uh, but is it okay if I offer you a little bit more information about the other vaccines that we're- we we